### Setup


In [2]:
import argparse
import os

import torchvision.transforms as transforms

from torch.utils.data import DataLoader
from torchvision import datasets

import torch

from gan import Gan

In [3]:
os.makedirs("images", exist_ok=True)

parser = argparse.ArgumentParser()
parser.add_argument('-f') # uncomment to run on colab/jupyter
parser.add_argument("--n_epochs", type=int, default=100, help="number of epochs of training")
parser.add_argument("--batch_size", type=int, default=128, help="size of the batches")
parser.add_argument("--lr", type=float, default=0.00005, help="learning rate")
parser.add_argument("--n_cpu", type=int, default=8, help="number of cpu threads to use during batch generation")
parser.add_argument("--latent_dim", type=int, default=100, help="dimensionality of the latent space")
parser.add_argument("--img_size", type=int, default=28, help="size of each image dimension")
parser.add_argument("--channels", type=int, default=1, help="number of image channels")
parser.add_argument("--n_critic", type=int, default=10, help="number of training steps for discriminator per iter")
parser.add_argument("--clip_value", type=float, default=0.01, help="lower and upper clip value for disc. weights")
parser.add_argument("--sample_interval", type=int, default=400, help="interval betwen image samples")
opt = parser.parse_args()
print(opt)

img_shape = (opt.channels, opt.img_size, opt.img_size)

Namespace(batch_size=128, channels=1, clip_value=0.01, f='/home/dany/.local/share/jupyter/runtime/kernel-a2369180-680d-438b-a439-c8d330f14b80.json', img_size=28, latent_dim=100, lr=5e-05, n_cpu=8, n_critic=10, n_epochs=100, sample_interval=400)


### Configure data loader

In [4]:
os.makedirs("data/mnist", exist_ok=True)
mnist_dataloader = torch.utils.data.DataLoader(
    datasets.MNIST(
        "data/mnist",
        train=True,
        download=True,
        transform=transforms.Compose([transforms.ToTensor(), transforms.Normalize([0.5], [0.5])]),
    ),
    batch_size=opt.batch_size,
    shuffle=True,
)


In [5]:
os.makedirs("data/celebA", exist_ok=True)
celeba_dataloader = torch.utils.data.DataLoader(
    datasets.CelebA(
        "data/celebA",
        #split="training",
        download=True, #True gives a Badzip error ==>
        # download the file from
        # https://drive.google.com/drive/folders/0B7EVK8r0v71pTUZsaXdaSnZBZzg?resourcekey=0-rJlzl934LzC-Xp28GeIBzQ
        # and save in the above folder
        transform=transforms.Compose([transforms.ToTensor(), transforms.Normalize([0.5], [0.5])]),
    ),
    batch_size=opt.batch_size,
    shuffle=True,
)


94616.0 bytess

Using downloaded and verified file: data/celebA/celeba/identity_CelebA.txt


94278.0 bytess

BadZipFile: File is not a zip file

### BGAN

In [ ]:
from nets.bgan_net import BGanGenerator, BGanDiscriminator

bGan_G = BGanGenerator(img_shape, opt.latent_dim)
bGan_D = BGanDiscriminator(img_shape)

bGan = Gan(bGan_G, bGan_D, opt.lr,dataset_name="celeba",loss_name="bgan") #mnist or celeba

dataloader =mnist_dataloader # or celeba_dataloader
b_list_loss_G,b_list_loss_D,b_list_Frech_dist = bGan.train(dataloader, opt.n_epochs, opt.clip_value, opt.n_critic, opt.sample_interval)

[Epoch 0/100] [Batch 0/469] [D loss: 0.11898717284202576] [G loss: 0.12626034021377563]
[FID 724.195496]
[Epoch 0/100] [Batch 50/469] [D loss: -0.3150690495967865] [G loss: 0.11142469942569733]
[Epoch 0/100] [Batch 100/469] [D loss: -0.3160299062728882] [G loss: 0.08976408839225769]
[Epoch 0/100] [Batch 150/469] [D loss: -0.2976326048374176] [G loss: 0.07785414904356003]
[Epoch 0/100] [Batch 200/469] [D loss: -0.2769698202610016] [G loss: 0.06917471438646317]
[Epoch 0/100] [Batch 250/469] [D loss: -0.25425562262535095] [G loss: 0.06059872731566429]
[Epoch 0/100] [Batch 300/469] [D loss: -0.23092015087604523] [G loss: 0.052030742168426514]
[Epoch 0/100] [Batch 350/469] [D loss: -0.20798859000205994] [G loss: 0.04485676437616348]
[Epoch 0/100] [Batch 400/469] [D loss: -0.19404813647270203] [G loss: 0.041516147553920746]
[FID 436.664246]
[Epoch 0/100] [Batch 450/469] [D loss: -0.17741836607456207] [G loss: 0.037543755024671555]


### Wasserstein

In [ ]:
from nets.wasserstein_net import WassersteinGenerator, WassersteinDiscriminator

wasserstein_G = WassersteinGenerator(img_shape, opt.latent_dim)
wasserstein_D = WassersteinDiscriminator(img_shape)

wasserstein_Gan = Gan(wasserstein_G, wasserstein_D, opt.lr, dataset_name="celeba", loss_name="wgan") #mnist or celeba

dataloader = celeba_dataloader # or celeba_dataloader
w_list_loss_G,w_list_loss_D,w_list_Frech_dist = wasserstein_Gan.train(dataloader, opt.n_epochs, opt.clip_value, opt.n_critic, opt.sample_interval)

In [7]:
import pandas as pd

b_loss_dict = {'b_loss_G': b_list_loss_G, 'b_loss_D' : b_list_loss_D,  }
df_b = pd.DataFrame(b_loss_dict)
df_b.to_csv(path_or_buf='results/bGAN.csv')

wass_loss_dict = {'wass_loss_G': w_list_loss_G, 'wass_loss_D' : w_list_loss_D,  }
df_w = pd.DataFrame(wass_loss_dict)
df_w.to_csv(path_or_buf='results/WGAN.csv')

dict_frech_dist = {'b_frech_dist':b_list_Frech_dist,'wass_frech_dist':w_list_Frech_dist}
df_frech_dist = pd.DataFrame(dict_frech_dist)
df_frech_dist.to_csv(path_or_buf='results/frech_dist.csv')

NameError: name 'b_list_loss_G' is not defined

## Results and Plot

In [26]:
import pandas as pd
import plotly.express as px

df = pd.read_csv('results/frech_dist.csv')

fig = px.line(df, y = ['wass_frech_dist','b_frech_dist'], title='Frechet Distance')
fig.show()








In [2]:
import pandas as pd
import plotly.express as px

df1 = pd.read_csv('results/bGAN.csv')
df2= pd.read_csv('results/WGAN.csv')
df = pd.concat([df1, df2], axis=1)
#df["wass_loss_G"] = -df["wass_loss_G"]
fig = px.line(df, y = ["b_loss_D","b_loss_G","wass_loss_G","wass_loss_D"], title='Losses')
fig.show()


